In [39]:
import pyodbc
import pandas as pd
import keras
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.layers import Embedding, LSTM, Dense
from keras.models import Sequential
from keras.models import load_model
import random
import numpy as np
import tensorflow as tf

server = 'cyse492group8.database.windows.net'
database = 'CYSE492_Project'
username = 'cyseadmin'
password = 'GroupProject492'
conn = pyodbc.connect('DRIVER={SQL Server};SERVER='+server+';DATABASE='+database+';UID='+username+';PWD='+ password)
cursor = conn.cursor()

In [10]:
cursor.execute("SELECT [Control Identifier],[Control Text]  FROM [dbo].['NIST_800.53_controls$']")

labels = []
texts = []
for row in cursor:
    texts.append(row[1])
    if 'AC' in row[0]:
        labels.append(1)
    if 'AT' in row[0]:
        labels.append(2)
    if 'AU' in row[0]:
        labels.append(3)
    if 'CA' in row[0]:
        labels.append(4)
    if 'CM' in row[0]:
        labels.append(5)
    if 'CP' in row[0]:
        labels.append(6)
    if 'IA' in row[0]:
        labels.append(7)
    if 'IR' in row[0]:
        labels.append(8)
    if 'MA' in row[0]:
        labels.append(9)
    if 'MP' in row[0]:
        labels.append(10)
    if 'PE' in row[0]:
        labels.append(11)
    if 'PL' in row[0]:
        labels.append(12)
    if 'PM' in row[0]:
        labels.append(13)
    if 'PS' in row[0]:
        labels.append(14)
    if 'PT' in row[0]:
        labels.append(15)
    if 'RA' in row[0]:
        labels.append(16)
    if 'SA' in row[0]:
        labels.append(17)
    if 'SC' in row[0]:
        labels.append(18)
    if 'SI' in row[0]:
        labels.append(19)
    if 'SR' in row[0]:
        labels.append(20)

x_test = []
y_test = []
labels3 = labels
x_act = np.array(texts)
y_act = np.array(labels)
print(len(labels))

1189


In [4]:
print(len((x_act)))
print(len((y_act)))

1189
1189


In [11]:
#Manually mapping cis

cursor.execute("SELECT TABLE_NAME FROM INFORMATION_SCHEMA.TABLES")

#Stuff Im giving to the model
cisNames = ["'CIS_Microsoft_Intune_for_Windows_10_Benchmark_v2.0.0 Level 1 (L1) - Corporate_Enter$'","'CIS_Apple_macOS_11.0_Benchmark_v1.2.0 Level 1$'",
            "'CIS_Apple_iOS_16_and_iPadOS_16_Benchmark_v1.1.0-EXCEL$'","'Prototype CIS Microsoft Intune for Windows 10 Release 2004 Benchmark v1.0.1_ARCHIVE Level 1 (L1)$'",
           "'Prototype_CIS_Microsoft_Windows_Server_2019_STIG_Benchmark_v1.0.0 Combined Profiles$'","'CIS_Ubuntu_Linux_20.04_LTS_STIG_Benchmark_v2.0.0 Level 1 - Server$'",
           "'CIS_SOPHOS_XG_Firewall_v18_Benchmark_v1.0.0_Level1$'","'CIS_Palo_Alto_Firewall_10_Benchmark_v1.0.0-FIXED_Level1$'","'CIS_Microsoft_Internet_Explorer_10_Benchmark_v1.0.0_ARCHIVE$'",
           "'CIS_Apple_macOS_10.15_Catalina_Benchmark_v3.0.0 Combined Profiles$'","'CIS_Check_Point_Firewall_Benchmark_v1.1.0_Level1$'","'CIS_Cisco_Firewall_Benchmark_v4.1.0_Certification_Level1$'",
           "'CIS_Fortigate_7.0.x_Benchmark_v1.2.0$'","'CIS_pfSense_Firewall_Benchmark_v1.1.0$'","'CIS_Microsoft_Windows_Server_2022_Benchmark_v2.0.0 Combined Profiles$'",
           "'CIS_Apple_iOS_16_and_iPadOS_16_Benchmark_v1.1.0-EXCEL$'","'CIS_Cisco_NX-OS_Benchmark_v1.0.0 EXCEL_Level2$'",
            "'CIS_Cisco_IOS_17.x_Benchmark_v2.0.0$'","'CIS_Apple_iOS_15_and_iPadOS_15_Benchmark_v1.1.0$'"]

#labels is the section num, texts is the description

#Get individual tables
setCount=0
for count in range(len(cisNames)):
    try:
        cursor.execute("SELECT [Section #], [Description]  FROM [dbo].["+cisNames[count]+"]")
        #checks and sorts by first number in the section number
        for row in cursor:
            if row[0] != None and row[1] != None and "This section is intentionally blank" not in row[1]:
                texts.append(str(row[1]))            
                if str(row[0])[0:2][-1] == ".":
                    labels.append(str(int(float(str(row[0])[0:3]))))#setCount)
                elif str(row[0])[0:3][-1] == ".":
                    labels.append(str(int(float(str(row[0])[0:4]))))#setCount)
                else:
                    labels.append(str(int(float(str(row[0])[0:2]))))#setCount)
            if len(texts) != len(labels):
                print("WARNNNING THEY FELL OFF HERE!:"+str(cisNames[count])+"      "+str(row[0])+" "+str(row[1]))
    except pyodbc.ProgrammingError:
        print(cisNames[count]+" is missing either description or label. Skipping")
x_act = np.array(texts)
y_act = np.array(labels)
print(len(labels))

5153


In [12]:
# Hyperparameters
max_words = 50000 # max number of words to use in the vocabulary was 15k
max_len = 400 # max length of each text (in terms of number of words) 250
embedding_dim = 400 # dimension of word embeddings was 100
lstm_units = 32 # number of units in the LSTM layer
# num_classes = len(set(labels)) + 1 # number of classes
num_classes = len(set(y_act)) + 1 # number of classes
#num_classes2 = len(set(y_test)) + 1

# Tokenize the texts and create a vocabulary
tokenizer = Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(x_act)
sequences = tokenizer.texts_to_sequences(x_act)

# Pad the sequences so they all have the same length
x = pad_sequences(sequences, maxlen=max_len)


# Create one-hot encoded labels
y = keras.utils.to_categorical(y_act, num_classes)

# y_test = keras.utils.to_categorical(y_test, num_classes)
# Build the model
model = Sequential()
model.add(Embedding(max_words, embedding_dim, input_length=max_len))
model.add(LSTM(lstm_units))
model.add(Dense(num_classes, activation='softmax'))

# Compile the model
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Train the model
history = model.fit(x, y, batch_size=32, epochs=20)# was 32,20




Epoch 1/20


162/162 [==============================] - 71s 411ms/step - loss: 2.0988 - accuracy: 0.3683
Epoch 2/20
162/162 [==============================] - 62s 384ms/step - loss: 1.2235 - accuracy: 0.6571
Epoch 3/20
162/162 [==============================] - 63s 388ms/step - loss: 0.7898 - accuracy: 0.7828
Epoch 4/20
162/162 [==============================] - 63s 389ms/step - loss: 0.5383 - accuracy: 0.8515
Epoch 5/20
162/162 [==============================] - 66s 406ms/step - loss: 0.3854 - accuracy: 0.8935
Epoch 6/20
162/162 [==============================] - 59s 365ms/step - loss: 0.2926 - accuracy: 0.9183
Epoch 7/20
162/162 [==============================] - 59s 363ms/step - loss: 0.2356 - accuracy: 0.9286
Epoch 8/20
162/162 [==============================] - 59s 361ms/step - loss: 0.1838 - accuracy: 0.9422
Epoch 9/20
162/162 [==============================] - 58s 361ms/step - loss: 0.1546 - accuracy: 0.9478
Epoch 10/20
162/162 [==============================] - 58s 359ms/step

In [13]:
#we like training
# Tokenize the texts and create a vocabulary
tokenizer = Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(x_act)
sequences = tokenizer.texts_to_sequences(x_act)

# Pad the sequences so they all have the same length
x = pad_sequences(sequences, maxlen=max_len)


# Create one-hot encoded labels
y = keras.utils.to_categorical(y_act, num_classes)

for loop10 in range(2):
    history = model.fit(x, y, batch_size=32, epochs=20)# was 32,20

Epoch 1/20
162/162 [==============================] - 56s 347ms/step - loss: 0.0775 - accuracy: 0.9639
Epoch 2/20
162/162 [==============================] - 56s 346ms/step - loss: 0.1007 - accuracy: 0.9559
Epoch 3/20
162/162 [==============================] - 59s 364ms/step - loss: 0.0674 - accuracy: 0.9670
Epoch 4/20
162/162 [==============================] - 60s 372ms/step - loss: 0.0578 - accuracy: 0.9678
Epoch 5/20
162/162 [==============================] - 57s 354ms/step - loss: 0.0536 - accuracy: 0.9684
Epoch 6/20
162/162 [==============================] - 55s 340ms/step - loss: 0.0540 - accuracy: 0.9684
Epoch 7/20
162/162 [==============================] - 55s 340ms/step - loss: 0.0499 - accuracy: 0.9713
Epoch 8/20
162/162 [==============================] - 55s 340ms/step - loss: 0.0475 - accuracy: 0.9707
Epoch 9/20
162/162 [==============================] - 55s 340ms/step - loss: 0.0465 - accuracy: 0.9711
Epoch 10/20
162/162 [==============================] - 55s 343ms/step - l

In [8]:
model.save('CYSE493_Group8_CISNISTEdit_Model.keras')

In [9]:
model = load_model('CYSE493_Group8_CISNISTEdit_Model.keras')

In [14]:
oldCis = cisNames

In [15]:
print(len(oldCis))

19


In [16]:
###padding
## reuse old tokenizer for x_test
tokenizer = Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(x_act)
sequences = tokenizer.texts_to_sequences(x_test)

## Pad the sequences so they all have the same length
x_test = pad_sequences(sequences, maxlen=max_len)
y_test = keras.utils.to_categorical(y_test, num_classes)

#Test the model     
#If you want to test different x_test/y_test you can compile that section instead of retraining the whole thing again
accr = model.evaluate(x_test,y_test) #x and y instead of test?
print('Test set\n  Loss: {:0.3f}\n  Accuracy: {:0.3f}'.format(accr[0],accr[1]))

#for i in range(10):
#    result = tf.argmax(model.predict(tf.expand_dims(texts[i], 0)), axis=1)
#    print(result.numpy(), labels[i])

ValueError: Expected input data to be non-empty.

In [17]:
#Train with CIS
server = 'cyse492group8.database.windows.net'
database = 'CYSE492_Project'
username = 'cyseadmin'
password = 'GroupProject492'
conn = pyodbc.connect('DRIVER={SQL Server};SERVER='+server+';DATABASE='+database+';UID='+username+';PWD='+ password)
cursor = conn.cursor()
#Get names of tables
cursor.execute("SELECT TABLE_NAME FROM INFORMATION_SCHEMA.TABLES")

cisNames = []
for names in cursor:
    if names[0]!=("'NIST_800.53_controls$'") and names[0]!="'NIST_800.53_baselines$'" and names[0] not in oldCis:
        cisNames.append(names[0])

#labels is the section num, texts is the description
setCount=0
labels = []
texts = []

#Get individual tables
for count in range(len(cisNames)):
    try:
        cursor.execute("SELECT [Section #], [Description]  FROM [dbo].["+cisNames[count]+"]")
        #checks and sorts by first number in the section number
        for row in cursor:
            if row[0] != None and row[1] != None and "This section is intentionally blank" not in row[1]:
                texts.append(str(row[1]))            
                if str(row[0])[0:2][-1] == ".":
                    labels.append(str(int(float(str(row[0])[0:3]))))#setCount)
                elif str(row[0])[0:3][-1] == ".":
                    labels.append(str(int(float(str(row[0])[0:4]))))#setCount)
                else:
                    labels.append(str(int(float(str(row[0])[0:2]))))#setCount)
            if len(texts) != len(labels):
                print("WARNNNING THEY FELL OFF HERE!:"+str(cisNames[count])+"      "+str(row[0])+" "+str(row[1]))
    except pyodbc.ProgrammingError:
        print(cisNames[count]+" is missing either description or label. Skipping")


x_test = []
y_test = []
x_cis = np.array(texts)
y_cis = np.array(labels)
y_cis = y_cis.astype(float)
y_cis = y_cis.astype(int)

# test is the actual test, act is used for the training
# for i in range(150):
#     random_index = random.randrange(len(labels))
#     x_test.append(texts.pop(random_index))
#     y_test.append(labels.pop(random_index))
# x_test = np.array(x_test)
# y_test = np.array(y_test)
# y_test = y_test.astype(float)
# y_test = y_test.astype(int)

'MITRE ATT&CK Filtering$' is missing either description or label. Skipping
'MITRE ATT&CK Filtering$'_xlnm#_FilterDatabase is missing either description or label. Skipping
CIS_Apple_macOS_12.0_Monterey_Benchmark_v3.0.0 License$ is missing either description or label. Skipping
'MITRE ATT&CK Mappings$' is missing either description or label. Skipping
'CIS_Apple_macOS_12.0_Monterey_Benchmark_v3.0.0 MITRE ATT&CK Filtering$' is missing either description or label. Skipping
'CIS_Apple_macOS_12.0_Monterey_Benchmark_v3.0.0 MITRE ATT&CK Filtering$'_xlnm#_FilterDatabase is missing either description or label. Skipping
'CIS_Apple_macOS_12.0_Monterey_Benchmark_v3.0.0 MITRE ATT&CK Mappings$' is missing either description or label. Skipping
'CIS_Apple_macOS_12.0_Monterey_Benchmark_v3.0.0 Overview - Glossary$' is missing either description or label. Skipping
CIS_Microsoft_Windows_Server_2019_STIG_Benchmark_v1.1.0 License$ is missing either description or label. Skipping
CIS_Apple_macOS_11.0_Big_Sur_Be

CIS_Microsoft_Intune_for_Windows_10_Benchmark_v2.0.0 License$ is missing either description or label. Skipping
mapping is missing either description or label. Skipping
sysdiagrams is missing either description or label. Skipping
CIS_BenchmarkPolicies is missing either description or label. Skipping
'CIS_Microsoft_Windows_Server_2003_Benchmark__imported__v3.1.0_ARCHIVE$' is missing either description or label. Skipping
'CIS_Microsoft_Windows_Server_2003__imported__v3.0.0_ARCHIVE$' is missing either description or label. Skipping
NIST_DefAndLabels is missing either description or label. Skipping
'CIS_Microsoft_Windows_Server_2008_R2__imported__v2.0.0_ARCHIVE$' is missing either description or label. Skipping
'CIS_Microsoft_Windows_Server_2008_Benchmark__imported__v2.1.0_ARCHIVE$' is missing either description or label. Skipping
CIS_Control_Test Sheets is missing either description or label. Skipping
NistConnections is missing either description or label. Skipping
CIS_Microsoft_Intune_for

In [18]:
texts2 = []
labels2 = []

for count in range(len(cisNames)):
    try:
        cursor.execute("SELECT [Section #], [Description]  FROM [dbo].["+cisNames[count]+"]")
        
        for row in cursor:
            if row[0] != None and row[1] != None and "This section is intentionally blank" not in row[1]:
                texts2.append(str(row[1]))
                labels2.append(str(row[0]))
    except pyodbc.ProgrammingError:
        print("*", end = " ")


* * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * 

In [19]:
print(len(texts2))

41055


In [20]:
texts2 = [s.replace("'", "''") for s in texts2]

In [158]:
string2 = '''
                  INSERT INTO CIS_BenchmarkPolicies (count, definitions, policyID)
                  VALUES
                          ({}, '{}', '{}')
                
                '''

for i in range(5,len(texts2)):
    cursor.execute(string2.format(i,texts2[i], labels2[i]))
    conn.commit()

In [161]:
cursor.execute('SELECT * FROM [dbo].[CIS_BenchmarkPolicies]')
for row in cursor:
    print(row[0])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097
2098
2099
2100
2101
2102
2103
2104
2105
2106
2107
2108
2109
2110
2111
2112
2113
2114
2115
2116
2117
2118
2119
2120
2121
2122
2123
2124
2125
2126
2127
2128
2129
2130
2131
2132
2133
2134
2135
2136
2137
2138
2139
2140
2141
2142
2143
2144
2145
2146
2147
2148
2149
2150
2151
2152
2153
2154
2155
2156
2157
2158
2159
2160
2161
2162
2163
2164
2165
2166
2167
2168
2169
2170
2171
2172
2173
2174
2175
2176
2177
2178
2179
2180
2181
2182
2183
2184
2185
2186
2187
2188
2189
2190
2191
2192
2193
2194
2195
2196
2197
2198
2199
2200
2201
2202
2203
2204
2205
2206
2207
2208
2209
2210
2211
2212
2213
2214
2215
2216
2217
2218
2219
2220
2221
2222
2223
2224
2225
2226
2227
2228
2229
2230
2231
2232
2233
2234
2235
2236
2237
2238
2239
2240
2241
2242


4470
4471
4472
4473
4474
4475
4476
4477
4478
4479
4480
4481
4482
4483
4484
4485
4486
4487
4488
4489
4490
4491
4492
4493
4494
4495
4496
4497
4498
4499
4500
4501
4502
4503
4504
4505
4506
4507
4508
4509
4510
4511
4512
4513
4514
4515
4516
4517
4518
4519
4520
4521
4522
4523
4524
4525
4526
4527
4528
4529
4530
4531
4532
4533
4534
4535
4536
4537
4538
4539
4540
4541
4542
4543
4544
4545
4546
4547
4548
4549
4550
4551
4552
4553
4554
4555
4556
4557
4558
4559
4560
4561
4562
4563
4564
4565
4566
4567
4568
4569
4570
4571
4572
4573
4574
4575
4576
4577
4578
4579
4580
4581
4582
4583
4584
4585
4586
4587
4588
4589
4590
4591
4592
4593
4594
4595
4596
4597
4598
4599
4600
4601
4602
4603
4604
4605
4606
4607
4608
4609
4610
4611
4612
4613
4614
4615
4616
4617
4618
4619
4620
4621
4622
4623
4624
4625
4626
4627
4628
4629
4630
4631
4632
4633
4634
4635
4636
4637
4638
4639
4640
4641
4642
4643
4644
4645
4646
4647
4648
4649
4650
4651
4652
4653
4654
4655
4656
4657
4658
4659
4660
4661
4662
4663
4664
4665
4666
4667
4668
4669


6722
6723
6724
6725
6726
6727
6728
6729
6730
6731
6732
6733
6734
6735
6736
6737
6738
6739
6740
6741
6742
6743
6744
6745
6746
6747
6748
6749
6750
6751
6752
6753
6754
6755
6756
6757
6758
6759
6760
6761
6762
6763
6764
6765
6766
6767
6768
6769
6770
6771
6772
6773
6774
6775
6776
6777
6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921


8386
8387
8388
8389
8390
8391
8392
8393
8394
8395
8396
8397
8398
8399
8400
8401
8402
8403
8404
8405
8406
8407
8408
8409
8410
8411
8412
8413
8414
8415
8416
8417
8418
8419
8420
8421
8422
8423
8424
8425
8426
8427
8428
8429
8430
8431
8432
8433
8434
8435
8436
8437
8438
8439
8440
8441
8442
8443
8444
8445
8446
8447
8448
8449
8450
8451
8452
8453
8454
8455
8456
8457
8458
8459
8460
8461
8462
8463
8464
8465
8466
8467
8468
8469
8470
8471
8472
8473
8474
8475
8476
8477
8478
8479
8480
8481
8482
8483
8484
8485
8486
8487
8488
8489
8490
8491
8492
8493
8494
8495
8496
8497
8498
8499
8500
8501
8502
8503
8504
8505
8506
8507
8508
8509
8510
8511
8512
8513
8514
8515
8516
8517
8518
8519
8520
8521
8522
8523
8524
8525
8526
8527
8528
8529
8530
8531
8532
8533
8534
8535
8536
8537
8538
8539
8540
8541
8542
8543
8544
8545
8546
8547
8548
8549
8550
8551
8552
8553
8554
8555
8556
8557
8558
8559
8560
8561
8562
8563
8564
8565
8566
8567
8568
8569
8570
8571
8572
8573
8574
8575
8576
8577
8578
8579
8580
8581
8582
8583
8584
8585


...

33985
33986
33987
33988
33989
33990
33991
33992
33993
33994
33995
33996
33997
33998
33999
34000
34001
34002
34003
34004
34005
34006
34007
34008
34009
34010
34011
34012
34013
34014
34015
34016
34017
34018
34019
34020
34021
34022
34023
34024
34025
34026
34027
34028
34029
34030
34031
34032
34033
34034
34035
34036
34037
34038
34039
34040
34041
34042
34043
34044
34045
34046
34047
34048
34049
34050
34051
34052
34053
34054
34055
34056
34057
34058
34059
34060
34061
34062
34063
34064
34065
34066
34067
34068
34069
34070
34071
34072
34073
34074
34075
34076
34077
34078
34079
34080
34081
34082
34083
34084
34085
34086
34087
34088
34089
34090
34091
34092
34093
34094
34095
34096
34097
34098
34099
34100
34101
34102
34103
34104
34105
34106
34107
34108
34109
34110
34111
34112
34113
34114
34115
34116
34117
34118
34119
34120
34121
34122
34123
34124
34125
34126
34127
34128
34129
34130
34131
34132
34133
34134
34135
34136
34137
34138
34139
34140
34141
34142
34143
34144
34145
34146
34147
34148
34149
34150
3415

35709
35710
35711
35712
35713
35714
35715
35716
35717
35718
35719
35720
35721
35722
35723
35724
35725
35726
35727
35728
35729
35730
35731
35732
35733
35734
35735
35736
35737
35738
35739
35740
35741
35742
35743
35744
35745
35746
35747
35748
35749
35750
35751
35752
35753
35754
35755
35756
35757
35758
35759
35760
35761
35762
35763
35764
35765
35766
35767
35768
35769
35770
35771
35772
35773
35774
35775
35776
35777
35778
35779
35780
35781
35782
35783
35784
35785
35786
35787
35788
35789
35790
35791
35792
35793
35794
35795
35796
35797
35798
35799
35800
35801
35802
35803
35804
35805
35806
35807
35808
35809
35810
35811
35812
35813
35814
35815
35816
35817
35818
35819
35820
35821
35822
35823
35824
35825
35826
35827
35828
35829
35830
35831
35832
35833
35834
35835
35836
35837
35838
35839
35840
35841
35842
35843
35844
35845
35846
35847
35848
35849
35850
35851
35852
35853
35854
35855
35856
35857
35858
35859
35860
35861
35862
35863
35864
35865
35866
35867
35868
35869
35870
35871
35872
35873
35874
3587

37244
37245
37246
37247
37248
37249
37250
37251
37252
37253
37254
37255
37256
37257
37258
37259
37260
37261
37262
37263
37264
37265
37266
37267
37268
37269
37270
37271
37272
37273
37274
37275
37276
37277
37278
37279
37280
37281
37282
37283
37284
37285
37286
37287
37288
37289
37290
37291
37292
37293
37294
37295
37296
37297
37298
37299
37300
37301
37302
37303
37304
37305
37306
37307
37308
37309
37310
37311
37312
37313
37314
37315
37316
37317
37318
37319
37320
37321
37322
37323
37324
37325
37326
37327
37328
37329
37330
37331
37332
37333
37334
37335
37336
37337
37338
37339
37340
37341
37342
37343
37344
37345
37346
37347
37348
37349
37350
37351
37352
37353
37354
37355
37356
37357
37358
37359
37360
37361
37362
37363
37364
37365
37366
37367
37368
37369
37370
37371
37372
37373
37374
37375
37376
37377
37378
37379
37380
37381
37382
37383
37384
37385
37386
37387
37388
37389
37390
37391
37392
37393
37394
37395
37396
37397
37398
37399
37400
37401
37402
37403
37404
37405
37406
37407
37408
37409
3741

38719
38720
38721
38722
38723
38724
38725
38726
38727
38728
38729
38730
38731
38732
38733
38734
38735
38736
38737
38738
38739
38740
38741
38742
38743
38744
38745
38746
38747
38748
38749
38750
38751
38752
38753
38754
38755
38756
38757
38758
38759
38760
38761
38762
38763
38764
38765
38766
38767
38768
38769
38770
38771
38772
38773
38774
38775
38776
38777
38778
38779
38780
38781
38782
38783
38784
38785
38786
38787
38788
38789
38790
38791
38792
38793
38794
38795
38796
38797
38798
38799
38800
38801
38802
38803
38804
38805
38806
38807
38808
38809
38810
38811
38812
38813
38814
38815
38816
38817
38818
38819
38820
38821
38822
38823
38824
38825
38826
38827
38828
38829
38830
38831
38832
38833
38834
38835
38836
38837
38838
38839
38840
38841
38842
38843
38844
38845
38846
38847
38848
38849
38850
38851
38852
38853
38854
38855
38856
38857
38858
38859
38860
38861
38862
38863
38864
38865
38866
38867
38868
38869
38870
38871
38872
38873
38874
38875
38876
38877
38878
38879
38880
38881
38882
38883
38884
3888

40325
40326
40327
40328
40329
40330
40331
40332
40333
40334
40335
40336
40337
40338
40339
40340
40341
40342
40343
40344
40345
40346
40347
40348
40349
40350
40351
40352
40353
40354
40355
40356
40357
40358
40359
40360
40361
40362
40363
40364
40365
40366
40367
40368
40369
40370
40371
40372
40373
40374
40375
40376
40377
40378
40379
40380
40381
40382
40383
40384
40385
40386
40387
40388
40389
40390
40391
40392
40393
40394
40395
40396
40397
40398
40399
40400
40401
40402
40403
40404
40405
40406
40407
40408
40409
40410
40411
40412
40413
40414
40415
40416
40417
40418
40419
40420
40421
40422
40423
40424
40425
40426
40427
40428
40429
40430
40431
40432
40433
40434
40435
40436
40437
40438
40439
40440
40441
40442
40443
40444
40445
40446
40447
40448
40449
40450
40451
40452
40453
40454
40455
40456
40457
40458
40459
40460
40461
40462
40463
40464
40465
40466
40467
40468
40469
40470
40471
40472
40473
40474
40475
40476
40477
40478
40479
40480
40481
40482
40483
40484
40485
40486
40487
40488
40489
40490
4049

In [79]:
print(len((x_act)))
print(len((y_act)))
print(len((x_cis)))
print(len((y_cis)))
print(len(cisNames))
print(cisNames[13])
# for dist in y_act:
     # print(dist)

5153
5153
41055
41055
278
CIS_Microsoft_Windows_Server_2019_STIG_Benchmark_v1.1.0 Combined$


In [80]:
#model.save('CYSE493_Group8_CIS-NIST_Model.keras')  # creates a keras save file
# identical to the previous one
#model = load_model('CYSE493_Group8_CIS-NIST_Model.keras')
print(len(set(y_act)))

20


In [37]:
#new tests
###padding
num_classes = len(set(y_act)) + 1 # number of classes

## reuse old tokenizer for x_test
tokenizer = Tokenizer(num_words=50000)#max_words)
tokenizer.fit_on_texts(x_act)#x_cis
sequences = tokenizer.texts_to_sequences(x_cis)

## Pad the sequences so they all have the same length
x_test = pad_sequences(sequences, maxlen=400)
y_test = keras.utils.to_categorical(y_cis, num_classes)

#Test the model     
#If you want to test different x_test/y_test you can compile that section instead of retraining the whole thing again
accr = model.evaluate(x_test,y_test) #was x_test and y_test?
print('Test set\n  Loss: {:0.3f}\n  Accuracy: {:0.3f}'.format(accr[0],accr[1]))
res = 0
final = []
finalCis = []
count = 0
random_numbers = np.random.choice(len(x_test), size=5000, replace=False)
for i in range(random_numbers):
    result = tf.argmax(model.predict(tf.expand_dims(x_test[i], 0)), axis=1)
    resnum = result.numpy()
    finalCis.append(labels2[i])
    final.append(resnum[0])
    count+=1
    print(count)
    #if (int(resnum[0]) == int(y_act[i])):
    #    res = res + 1
    


1283/1283 [==============================] - 98s 76ms/step - loss: 0.5123 - accuracy: 0.9260
Test set
  Loss: 0.512
  Accuracy: 0.926
1/1 [==============================] - 0s 62ms/step
1
1/1 [==============================] - 0s 56ms/step
2
1/1 [==============================] - 0s 59ms/step
3
1/1 [==============================] - 0s 57ms/step
4
1/1 [==============================] - 0s 68ms/step
5
1/1 [==============================] - 0s 63ms/step
6
1/1 [==============================] - 0s 72ms/step
7
1/1 [==============================] - 0s 55ms/step
8
1/1 [==============================] - 0s 77ms/step
9
1/1 [==============================] - 0s 57ms/step
10
1/1 [==============================] - 0s 60ms/step
11
1/1 [==============================] - 0s 71ms/step
12
1/1 [==============================] - 0s 58ms/step
13
1/1 [==============================] - 0s 66ms/step
14
1/1 [==============================] - 0s 58ms/step
15
1/1 [==============================] - 0s 70ms/ste

1/1 [==============================] - 0s 79ms/step
146
1/1 [==============================] - 0s 81ms/step
147
1/1 [==============================] - 0s 69ms/step
148
1/1 [==============================] - 0s 60ms/step
149
1/1 [==============================] - 0s 79ms/step
150
1/1 [==============================] - 0s 70ms/step
151
1/1 [==============================] - 0s 80ms/step
152
1/1 [==============================] - 0s 61ms/step
153
1/1 [==============================] - 0s 73ms/step
154
1/1 [==============================] - 0s 88ms/step
155
1/1 [==============================] - 0s 78ms/step
156
1/1 [==============================] - 0s 78ms/step
157
1/1 [==============================] - 0s 69ms/step
158
1/1 [==============================] - 0s 74ms/step
159
1/1 [==============================] - 0s 83ms/step
160
1/1 [==============================] - 0s 63ms/step
161
1/1 [==============================] - 0s 57ms/step
162
1/1 [==============================] - 0s 73ms/s

1/1 [==============================] - 0s 66ms/step
292
1/1 [==============================] - 0s 73ms/step
293
1/1 [==============================] - 0s 78ms/step
294
1/1 [==============================] - 0s 74ms/step
295
1/1 [==============================] - 0s 57ms/step
296
1/1 [==============================] - 0s 76ms/step
297
1/1 [==============================] - 0s 57ms/step
298
1/1 [==============================] - 0s 76ms/step
299
1/1 [==============================] - 0s 54ms/step
300
1/1 [==============================] - 0s 51ms/step
301
1/1 [==============================] - 0s 62ms/step
302
1/1 [==============================] - 0s 70ms/step
303
1/1 [==============================] - 0s 55ms/step
304
1/1 [==============================] - 0s 56ms/step
305
1/1 [==============================] - 0s 70ms/step
306
1/1 [==============================] - 0s 63ms/step
307
1/1 [==============================] - 0s 54ms/step
308
1/1 [==============================] - 0s 64ms/s

1/1 [==============================] - 0s 58ms/step
438
1/1 [==============================] - 0s 65ms/step
439
1/1 [==============================] - 0s 71ms/step
440
1/1 [==============================] - 0s 60ms/step
441
1/1 [==============================] - 0s 65ms/step
442
1/1 [==============================] - 0s 56ms/step
443
1/1 [==============================] - 0s 58ms/step
444
1/1 [==============================] - 0s 62ms/step
445
1/1 [==============================] - 0s 58ms/step
446
1/1 [==============================] - 0s 53ms/step
447
1/1 [==============================] - 0s 62ms/step
448
1/1 [==============================] - 0s 54ms/step
449
1/1 [==============================] - 0s 59ms/step
450
1/1 [==============================] - 0s 80ms/step
451
1/1 [==============================] - 0s 54ms/step
452
1/1 [==============================] - 0s 53ms/step
453
1/1 [==============================] - 0s 58ms/step
454
1/1 [==============================] - 0s 69ms/s

1/1 [==============================] - 0s 64ms/step
584
1/1 [==============================] - 0s 95ms/step
585
1/1 [==============================] - 0s 54ms/step
586
1/1 [==============================] - 0s 68ms/step
587
1/1 [==============================] - 0s 79ms/step
588
1/1 [==============================] - 0s 69ms/step
589
1/1 [==============================] - 0s 65ms/step
590
1/1 [==============================] - 0s 73ms/step
591
1/1 [==============================] - 0s 62ms/step
592
1/1 [==============================] - 0s 67ms/step
593
1/1 [==============================] - 0s 56ms/step
594
1/1 [==============================] - 0s 79ms/step
595
1/1 [==============================] - 0s 64ms/step
596
1/1 [==============================] - 0s 59ms/step
597
1/1 [==============================] - 0s 61ms/step
598
1/1 [==============================] - 0s 68ms/step
599
1/1 [==============================] - 0s 69ms/step
600
1/1 [==============================] - 0s 77ms/s

...

1/1 [==============================] - 0s 58ms/step
40487
1/1 [==============================] - 0s 52ms/step
40488
1/1 [==============================] - 0s 54ms/step
40489
1/1 [==============================] - 0s 52ms/step
40490
1/1 [==============================] - 0s 52ms/step
40491
1/1 [==============================] - 0s 59ms/step
40492
1/1 [==============================] - 0s 56ms/step
40493
1/1 [==============================] - 0s 59ms/step
40494
1/1 [==============================] - 0s 64ms/step
40495
1/1 [==============================] - 0s 53ms/step
40496
1/1 [==============================] - 0s 50ms/step
40497
1/1 [==============================] - 0s 56ms/step
40498
1/1 [==============================] - 0s 55ms/step
40499
1/1 [==============================] - 0s 57ms/step
40500
1/1 [==============================] - 0s 53ms/step
40501
1/1 [==============================] - 0s 53ms/step
40502
1/1 [==============================] - 0s 54ms/step
40503
1/1 [=========

1/1 [==============================] - 0s 62ms/step
40628
1/1 [==============================] - 0s 57ms/step
40629
1/1 [==============================] - 0s 54ms/step
40630
1/1 [==============================] - 0s 64ms/step
40631
1/1 [==============================] - 0s 62ms/step
40632
1/1 [==============================] - 0s 62ms/step
40633
1/1 [==============================] - 0s 59ms/step
40634
1/1 [==============================] - 0s 57ms/step
40635
1/1 [==============================] - 0s 59ms/step
40636
1/1 [==============================] - 0s 59ms/step
40637
1/1 [==============================] - 0s 53ms/step
40638
1/1 [==============================] - 0s 54ms/step
40639
1/1 [==============================] - 0s 58ms/step
40640
1/1 [==============================] - 0s 59ms/step
40641
1/1 [==============================] - 0s 60ms/step
40642
1/1 [==============================] - 0s 63ms/step
40643
1/1 [==============================] - 0s 66ms/step
40644
1/1 [=========

1/1 [==============================] - 0s 51ms/step
40769
1/1 [==============================] - 0s 55ms/step
40770
1/1 [==============================] - 0s 57ms/step
40771
1/1 [==============================] - 0s 60ms/step
40772
1/1 [==============================] - 0s 56ms/step
40773
1/1 [==============================] - 0s 56ms/step
40774
1/1 [==============================] - 0s 61ms/step
40775
1/1 [==============================] - 0s 54ms/step
40776
1/1 [==============================] - 0s 54ms/step
40777
1/1 [==============================] - 0s 60ms/step
40778
1/1 [==============================] - 0s 51ms/step
40779
1/1 [==============================] - 0s 53ms/step
40780
1/1 [==============================] - 0s 58ms/step
40781
1/1 [==============================] - 0s 52ms/step
40782
1/1 [==============================] - 0s 63ms/step
40783
1/1 [==============================] - 0s 53ms/step
40784
1/1 [==============================] - 0s 56ms/step
40785
1/1 [=========

1/1 [==============================] - 0s 69ms/step
40910
1/1 [==============================] - 0s 56ms/step
40911
1/1 [==============================] - 0s 59ms/step
40912
1/1 [==============================] - 0s 61ms/step
40913
1/1 [==============================] - 0s 62ms/step
40914
1/1 [==============================] - 0s 61ms/step
40915
1/1 [==============================] - 0s 67ms/step
40916
1/1 [==============================] - 0s 56ms/step
40917
1/1 [==============================] - 0s 55ms/step
40918
1/1 [==============================] - 0s 66ms/step
40919
1/1 [==============================] - 0s 72ms/step
40920
1/1 [==============================] - 0s 68ms/step
40921
1/1 [==============================] - 0s 59ms/step
40922
1/1 [==============================] - 0s 58ms/step
40923
1/1 [==============================] - 0s 69ms/step
40924
1/1 [==============================] - 0s 53ms/step
40925
1/1 [==============================] - 0s 61ms/step
40926
1/1 [=========

1/1 [==============================] - 0s 67ms/step
41051
1/1 [==============================] - 0s 56ms/step
41052
1/1 [==============================] - 0s 58ms/step
41053
1/1 [==============================] - 0s 62ms/step
41054
1/1 [==============================] - 0s 56ms/step
41055


In [24]:
print(len(final))
print(finalCis)

5000
['19.6.6.1', '18.5', '18.10.57.3.10', '1.3', '2.3.6', '9.3', '4.1', '18.6.23.2', '2.3.17', '18.8.5', '18.5.5', '18.9.20.1', '2.3.8', '18.10', '18.6.21', '19.7.42', '2.3.1', '18.9.65.3.10', '2.2', '18.10.57.2', '18.9.84', '2.3.1', '2.3.11', '18.10.15', '1.2', '19.1.3', '9.3', '2.11', '2.3.7', '18.9.35', '2.2', '18.10.63', '9.1', '17.2', '2.3.1', '18.10.26.3', '4.5.1', '6.2', '18.9.45.10', '18.10.43.6.1', '18.1', '18.8', '18.5', '1', '18.10.7', '20', '2.3.7', '2.3.8', '18.5', '18.1.1', '18.10.57.3.9', '18.3', '17.9', '2.3.9', '18.10.89.1', '18.9.14', '18.5.11', '2.3.6', '9.2', '2.2', '1.2', '18.9.27.3', '18.10.9.2', '18.9.55', '2.3.15', '18.9.5', '2.2', '18.5', '18.9.102.1', '19', '2.17', '18.10.81', '9.1', '2.3', '18.10.58.3.2', '18.10.81', '18.8.28', '17.3', '9.2', '19.7.39', '18.8.1', '18.9.5', '18.4', '18.9.65.3.11', '9.1', '18.8.22.1', '2.5', '18.9.62.3.9', '18.8.26', '5.1.1', '2.2', '2.3.9', '17.7', '2.3.17', '9.1', '18.3', '18.9.46.11', '18.8.21', '18.10.67', '9.1', '19.6', '

In [41]:
label_to_string = {
    1: 'AC',
    2: 'AT',
    3: 'AU',
    4: 'CA',
    5: 'CM',
    6: 'CP',
    7: 'IA',
    8: 'IR',
    9: 'MA',
    10: 'MP',
    11: 'PE',
    12: 'PL',
    13: 'PM',
    14: 'PS',
    15: 'PT',
    16: 'RA',
    17: 'SA',
    18: 'SC',
    19: 'SI',
    20: 'SR'
}

array_of_string_labels = [label_to_string[number] for number in final]

# Now array_of_string_labels contains string labels corresponding to each number in array_of_numbers
print(len(array_of_string_labels))

41055


In [104]:
string2 = '''
                  INSERT INTO mapping (count, policyID, controlID)
                  VALUES
                          ({}, {}, {})
                
                '''

cursor.execute('''
                  INSERT INTO mapping (count, policyID, controlID)
                  VALUES
                          ({}, {}, {})
                
                ''').format()



for i in range(len(finalCis)):
    cursor.execute(string2.format())

<function Connection.commit>

In [103]:
print(max(array_of_string_labels, key=len))

SC


In [101]:
type(final)

list

In [110]:
print(len(finalCis))

1000


In [42]:
string2 = '''
                  INSERT INTO mapping_final (count, policyID, controlID)
                  VALUES
                          ({}, '{}', '{}')
                
                '''
#print(string2.format(0,finalCis[0], array_of_string_labels[0]))

for i in range(0, len(finalCis)):
    cursor.execute(string2.format(i,finalCis[i], array_of_string_labels[i]))
    conn.commit()

In [28]:
cursor.execute('SELECT * FROM [dbo].[mapping_5000]')
for row in cursor:
    print(row)

(0, '19.6.6.1', 'SI')
(1, '18.5', 'SC')
(2, '18.10.57.3.10', 'SC')
(3, '1.3', 'AC')
(4, '2.3.6', 'AT')
(5, '9.3', 'MA')
(6, '4.1', 'CA')
(7, '18.6.23.2', 'SC')
(8, '2.3.17', 'AT')
(9, '18.8.5', 'SC')
(10, '18.5.5', 'SC')
(11, '18.9.20.1', 'SC')
(12, '2.3.8', 'AT')
(13, '18.10', 'SC')
(14, '18.6.21', 'SC')
(15, '19.7.42', 'SI')
(16, '2.3.1', 'AT')
(17, '18.9.65.3.10', 'SC')
(18, '2.2', 'AT')
(19, '18.10.57.2', 'SC')
(20, '18.9.84', 'SC')
(21, '2.3.1', 'AT')
(22, '2.3.11', 'AT')
(23, '18.10.15', 'SC')
(24, '1.2', 'AC')
(25, '19.1.3', 'SI')
(26, '9.3', 'MA')
(27, '2.11', 'AC')
(28, '2.3.7', 'AT')
(29, '18.9.35', 'SC')
(30, '2.2', 'AT')
(31, '18.10.63', 'SC')
(32, '9.1', 'MA')
(33, '17.2', 'SA')
(34, '2.3.1', 'AT')
(35, '18.10.26.3', 'SC')
(36, '4.5.1', 'CA')
(37, '6.2', 'CP')
(38, '18.9.45.10', 'SC')
(39, '18.10.43.6.1', 'SC')
(40, '18.1', 'SC')
(41, '18.8', 'SC')
(42, '18.5', 'SC')
(43, '1', 'AC')
(44, '18.10.7', 'SC')
(45, '20', 'IA')
(46, '2.3.7', 'AT')
(47, '2.3.8', 'AT')
(48, '18.5',

(806, '2.3.17', 'AT')
(807, '18.10.93.2', 'SC')
(808, '1.3', 'AC')
(809, '18.10.57.3.2', 'SC')
(810, '1.3', 'AC')
(811, '2.3.8', 'AT')
(812, '2.3.13', 'AT')
(813, '9.1', 'MA')
(814, '2.2', 'AT')
(815, '18.9.34', 'SC')
(816, '2.7', 'AU')
(817, '5.2', 'CM')
(818, '18.6.9', 'SC')
(819, '18.10.82', 'SC')
(820, '5', 'AC')
(821, '1.1', 'AC')
(822, '2.2', 'AT')
(823, '20', 'SA')
(824, '19.5', 'SC')
(825, '3', 'CM')
(826, '2.3.4', 'AT')
(827, '2.2', 'AT')
(828, '17.8', 'SA')
(829, '18.6.19', 'SC')
(830, '18.10.57', 'SC')
(831, '18.9.99', 'SC')
(832, '18.8.47', 'SC')
(833, '18.9.65.3.3', 'SC')
(834, '2.2', 'AT')
(835, '18.9.28', 'SC')
(836, '2.3.1', 'AT')
(837, '18', 'SC')
(838, '7', 'AT')
(839, '18.9.50', 'SC')
(840, '9.2', 'MA')
(841, '18.9.5', 'SC')
(842, '18.9.7', 'SC')
(843, '2.3.9', 'AT')
(844, '18.10.63', 'SC')
(845, '2.2', 'AT')
(846, '19.6', 'SC')
(847, '18.9.26.4', 'SC')
(848, '18.9.99.2', 'SC')
(849, '18.9.14', 'SC')
(850, '2.3', 'AT')
(851, '5.5', 'CA')
(852, '18.10.82', 'SC')
(853,

(1571, '2.2', 'AT')
(1572, '2.3.8', 'AT')
(1573, '18.4', 'SC')
(1574, '18.9.45.4.3', 'SC')
(1575, '18.9.85', 'SC')
(1576, '9.3', 'MA')
(1577, '2.2', 'AT')
(1578, '18.10.12', 'SC')
(1579, '2.3.15', 'AT')
(1580, '2.2', 'AT')
(1581, '9.3', 'MA')
(1582, '18.8', 'SC')
(1583, '18.9.80.1', 'SC')
(1584, '2.3.10', 'AT')
(1585, '17.2', 'SA')
(1586, '18.9.17', 'SC')
(1587, '8.1', 'IR')
(1588, '18.10.93.2', 'SC')
(1589, '18.9.102.2', 'SC')
(1590, '1.5.1', 'AC')
(1591, '18.10.26.2', 'SC')
(1592, '2.3.9', 'AT')
(1593, '18.4', 'SC')
(1594, '1.2', 'AC')
(1595, '18.10.57.3.2', 'SC')
(1596, '19.1.3', 'SI')
(1597, '7.2', 'IR')
(1598, '9.2', 'MA')
(1599, '18.10.9.2', 'SC')
(1600, '18.9.46.5', 'SC')
(1601, '18.9.30', 'SC')
(1602, '3', 'AU')
(1603, '2.3.6', 'AT')
(1604, '18.10.89.1', 'SC')
(1605, '17.6', 'SA')
(1606, '19.7.42', 'SC')
(1607, '9.2', 'MA')
(1608, '18.10.17', 'SC')
(1609, '2.2', 'AC')
(1610, '2.2', 'AT')
(1611, '18.9.32.6', 'SC')
(1612, '18.10.14', 'SC')
(1613, '2.3.1', 'AT')
(1614, '18.10.63',

(2235, '18.9.100', 'SC')
(2236, '18.6.4', 'SC')
(2237, '2.15', 'AT')
(2238, '2.2', 'AT')
(2239, '17.7', 'SA')
(2240, '2.3.10', 'AT')
(2241, '2.3.9', 'AT')
(2242, '18.9.85.1', 'SC')
(2243, '1', 'AC')
(2244, '18.5.10', 'SC')
(2245, '2.2', 'AT')
(2246, '2.3.11', 'AT')
(2247, '2.3.8', 'AT')
(2248, '9.1', 'MA')
(2249, '20', 'SC')
(2250, '18.10.92.2', 'SC')
(2251, '2.2', 'AT')
(2252, '1.9.1', 'AC')
(2253, '18.5', 'SC')
(2254, '18.9.26', 'SC')
(2255, '18.8.36', 'SC')
(2256, '2.2', 'AT')
(2257, '2.2', 'AT')
(2258, '17.8', 'SA')
(2259, '18.10.76', 'SC')
(2260, '18.5.19.2', 'SC')
(2261, '3', 'AU')
(2262, '2.2', 'AT')
(2263, '18.7', 'SC')
(2264, '18.10.57.3.10', 'SC')
(2265, '18.8.52.1', 'SC')
(2266, '2.3.1', 'AT')
(2267, '18.9.26', 'SC')
(2268, '18.1.1', 'SC')
(2269, '1.1.2.3', 'AC')
(2270, '2.2', 'AT')
(2271, '18.10.93.4', 'SC')
(2272, '1.2', 'SI')
(2273, '18.5.19.2', 'SC')
(2274, '2.2', 'AT')
(2275, '18.6.5', 'SC')
(2276, '18.9.98', 'SC')
(2277, '18.6.14', 'SC')
(2278, '5.2', 'CA')
(2279, '18.

(2806, '18.9.37', 'SC')
(2807, '9.3', 'MA')
(2808, '2.3.2', 'AT')
(2809, '18.9.8', 'SC')
(2810, '18.4', 'SC')
(2811, '2.3.7', 'AT')
(2812, '2.3.6', 'AT')
(2813, '18.9.43', 'SC')
(2814, '1.1', 'AC')
(2815, '18.9.62.3.2', 'SC')
(2816, '2.3.5', 'AT')
(2817, '18.8.28', 'SC')
(2818, '8.3', 'IR')
(2819, '18.10.58', 'SC')
(2820, '5.2', 'CA')
(2821, '18.7', 'SC')
(2822, '18.6.19.2', 'SC')
(2823, '18.9.46.5', 'SC')
(2824, '1.1', 'AC')
(2825, '18.5', 'SC')
(2826, '18.8.48.5', 'SC')
(2827, '1.1', 'AC')
(2828, '19.7.42.2', 'SI')
(2829, '18.9.27', 'SC')
(2830, '18.10.4', 'SC')
(2831, '18.9.65.3.11', 'SC')
(2832, '3', 'AU')
(2833, '5.2.4', 'CM')
(2834, '18.6.14', 'SC')
(2835, '18.1.2', 'SC')
(2836, '1.10', 'AC')
(2837, '18.8.34', 'SC')
(2838, '18.10.26.1', 'SC')
(2839, '18.9.69', 'SC')
(2840, '5', 'IA')
(2841, '18.10.5', 'SC')
(2842, '1.1', 'AC')
(2843, '18.10.58', 'SC')
(2844, '18.1.1', 'SC')
(2845, '18', 'SC')
(2846, '18.10.76.2', 'SC')
(2847, '18.10.13', 'SC')
(2848, '9.3', 'MA')
(2849, '1.1', 'A

(3508, '18.10.93.2', 'SC')
(3509, '18.8.22.1', 'SC')
(3510, '18.10.57.3.11', 'SC')
(3511, '5', 'AT')
(3512, '18', 'SC')
(3513, '18.10.58.3.9', 'SC')
(3514, '18.3', 'SC')
(3515, '18.9.45.11', 'SC')
(3516, '2.10', 'AT')
(3517, '18.9.45.8', 'SC')
(3518, '18.9.47', 'SC')
(3519, '2.2', 'AT')
(3520, '2.3.1', 'AT')
(3521, '18.10.77.2', 'SC')
(3522, '2.3.9', 'AT')
(3523, '18.10.58.3.2', 'SC')
(3524, '18.9.32.6', 'SC')
(3525, '18.10.94.4', 'SC')
(3526, '2.2', 'AT')
(3527, '18.9.65.3.10', 'SC')
(3528, '18.7', 'SC')
(3529, '2.2', 'AT')
(3530, '2.3.17', 'AT')
(3531, '1', 'AC')
(3532, '2.2', 'AT')
(3533, '18.6.19', 'SC')
(3534, '2.6.1', 'AT')
(3535, '18.9.62.3.9', 'SC')
(3536, '18.8.25', 'SC')
(3537, '18.10.15', 'SC')
(3538, '18.9.27', 'SC')
(3539, '2.2', 'AT')
(3540, '18.8.3', 'SC')
(3541, '18.1', 'SC')
(3542, '4.4.3', 'CA')
(3543, '17.8', 'SA')
(3544, '17.6', 'SA')
(3545, '18.9.27', 'SC')
(3546, '18.10.26.4', 'SC')
(3547, '18.10.57', 'SC')
(3548, '18.5.11', 'SC')
(3549, '18.9.62.3.3', 'SC')
(3550

(4132, '3', 'CA')
(4133, '18.9.20.1', 'SC')
(4134, '18.9.7.1', 'SC')
(4135, '18.8.4', 'SC')
(4136, '2.2', 'AT')
(4137, '20', 'AC')
(4138, '2.3.7', 'AT')
(4139, '2.2', 'AT')
(4140, '18.8.5', 'SC')
(4141, '18.6.4', 'SC')
(4142, '18.10.29', 'SC')
(4143, '18.8.21', 'SC')
(4144, '18.6', 'SC')
(4145, '18.10.57.3.10', 'SC')
(4146, '19', 'SI')
(4147, '18.10.89.1', 'SC')
(4148, '2.3.11', 'AT')
(4149, '18.10.79', 'SC')
(4150, '18.10.17', 'SC')
(4151, '18.8.22.1', 'SC')
(4152, '17.9', 'SA')
(4153, '18.8.4', 'SC')
(4154, '17.5', 'SA')
(4155, '18.10.67', 'SC')
(4156, '18.10.5', 'SC')
(4157, '18.9.20.1', 'SC')
(4158, '18.1.1', 'SC')
(4159, '18.6.19.2', 'SC')
(4160, '18.9.45.4', 'SC')
(4161, '18.9.34', 'SC')
(4162, '9.1', 'MA')
(4163, '18.9.65.2', 'SC')
(4164, '18.8.26', 'SC')
(4165, '18.10.58.2', 'SC')
(4166, '9.2', 'MA')
(4167, '18.3', 'SC')
(4168, '18.9.46', 'SC')
(4169, '18.10.4', 'SC')
(4170, '5.2.3', 'CM')
(4171, '18.10.26.3', 'SC')
(4172, '18.10.89.1', 'SC')
(4173, '9.2', 'MA')
(4174, '18.10.8

(4839, '18.8.28', 'SC')
(4840, '2.3.6', 'AT')
(4841, '18.9.39', 'SC')
(4842, '18.10.57.3', 'SC')
(4843, '18.8.22', 'SC')
(4844, '19.1.3', 'SI')
(4845, '9.3', 'MA')
(4846, '17.6', 'SA')
(4847, '18.9.99.2', 'SC')
(4848, '2.2', 'AT')
(4849, '7', 'IA')
(4850, '7', 'IA')
(4851, '3', 'AU')
(4852, '2.9.1', 'AT')
(4853, '18.10.8.1', 'SC')
(4854, '18.10.26.4', 'SC')
(4855, '18.10.26.1', 'SC')
(4856, '2.2', 'AT')
(4857, '2.13', 'IA')
(4858, '18.4', 'SC')
(4859, '17.3', 'SA')
(4860, '3.4.3.1', 'AU')
(4861, '17.5', 'SA')
(4862, '2.3.7', 'AT')
(4863, '20', 'SC')
(4864, '17.5', 'SA')
(4865, '19.1', 'SC')
(4866, '2.3.17', 'AT')
(4867, '18.9.46.5', 'SC')
(4868, '18.10.43.10', 'SC')
(4869, '19.7.4', 'SI')
(4870, '18.5.8', 'SC')
(4871, '18.4', 'SC')
(4872, '2.3.3', 'AT')
(4873, '2.2', 'AT')
(4874, '18.6.21', 'SC')
(4875, '18.9.27', 'SC')
(4876, '2.3.13', 'AT')
(4877, '1.2', 'AC')
(4878, '18.9.65.3.3', 'SC')
(4879, '2.3.14', 'CM')
(4880, '18.8.47', 'SC')
(4881, '2.3.2', 'AT')
(4882, '17.6', 'SA')
(4883, 

In [164]:
cursor.execute("SELECT [Control Identifier],[Control Text]  FROM [dbo].['NIST_800.53_controls$']")

texts3 = []
for row in cursor:
    texts3.append(row[1])

print(len(texts3))
print(len(labels3))

1189
1189


In [171]:
label_to_string = {
    1: 'AC',
    2: 'AT',
    3: 'AU',
    4: 'CA',
    5: 'CM',
    6: 'CP',
    7: 'IA',
    8: 'IR',
    9: 'MA',
    10: 'MP',
    11: 'PE',
    12: 'PL',
    13: 'PM',
    14: 'PS',
    15: 'PT',
    16: 'RA',
    17: 'SA',
    18: 'SC',
    19: 'SI',
    20: 'SR'
}

labels3 = [label_to_string[number] for number in labels3]

In [174]:
largest_string = max(texts3, key=len)
print(len(largest_string))

1980


In [176]:
string2 = '''
                  INSERT INTO NIST_DefAndLabels (count, definitions, controlID)
                  VALUES
                          ({}, '{}', '{}')
                
                '''

for i in range(0,len(texts3)):
    cursor.execute(string2.format(i,texts3[i], labels3[i]))
    conn.commit()

In [175]:
texts3 = [s.replace("'", "''") for s in texts3]

In [177]:
cursor.execute('SELECT * FROM [dbo].[NIST_DefAndLabels]')
for row in cursor:
    print(row)

(0, 'a. Develop, document, and disseminate to [Assignment: organization-defined personnel or roles]:\n1. [Selection (one or more): Organization-level; Mission/business process-level; System-level] access control policy that:\n(a) Addresses purpose, scope, roles, responsibilities, management commitment, coordination among organizational entities, and compliance; and\n(b) Is consistent with applicable laws, executive orders, directives, regulations, policies, standards, and guidelines; and\n2. Procedures to facilitate the implementation of the access control policy and the associated access controls;\nb. Designate an [Assignment: organization-defined official] to manage the development, documentation, and dissemination of the access control policy and procedures; and\nc. Review and update the current access control:\n1. Policy [Assignment: organization-defined frequency] and following [Assignment: organization-defined events]; and\n2. Procedures [Assignment: organization-defined frequenc

(640, 'Establish, maintain, and update [Assignment: organization-defined frequency] an inventory of all systems, applications, and projects that process personally identifiable information.', 'PM')
(641, 'Develop, monitor, and report on the results of information security and privacy measures of performance.', 'PM')
(642, 'Develop and maintain an enterprise architecture with consideration for information security, privacy, and the resulting risk to organizational operations and assets, individuals, other organizations, and the Nation.', 'PM')
(643, 'Offload [Assignment: organization-defined non-essential functions or services] to other systems, system components, or an external provider.', 'PM')
(644, 'Address information security and privacy issues in the development, documentation, and updating of a critical infrastructure and key resources protection plan.', 'PM')
(645, 'a. Develops a comprehensive strategy to manage:\n1. Security risk to organizational operations and assets, indivi

In [190]:
cursor.execute('SELECT * FROM [dbo].[CIS_Control_Test Sheets]')
count = 0
count = count + 1
for row in cursor:
    count = count + 1
    print('*', end = "")
print(count)

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

...

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

In [185]:


string1 = 'SELECT [Control ID] ,[Control Name] ,[Description] ,[Control Test] FROM [dbo].[CIS_Control_{}_Test Sheet1$]'

id = []
name = []
desc = []
test = []

for i in range(1,19):
    cursor.execute(string1.format(i))
    for row in cursor:
        id.append(row[0])
        name.append(row[1])
        desc.append(row[2])
        test.append(row[3])

In [6]:
nist_definitions = {
    'AC': 'Access Control',
    'AT': 'Awareness and Training',
    'AU': 'Audit and Accountability',
    'CA': 'Security Assessment and Authorization',
    'CM': 'Configuration Management',
    'CP': 'Contingency Planning',
    'IA': 'Identification and Authentication',
    'IR': 'Incident Response',
    'MA': 'Maintenance',
    'MP': 'Media Protection',
    'PE': 'Physical and Environmental Protection',
    'PL': 'Planning',
    'PM': 'Program Management',
    'PS': 'Personnel Security',
    'PT': 'System and Communications Protection',
    'RA': 'Risk Assessment',
    'SA': 'System and Services Acquisition',
    'SC': 'System and Communications',
    'SI': 'System and Information Integrity',
    'SR': 'Supply Chain Risk Management'
}

In [8]:
string2 = '''
                  INSERT INTO NISTConnections (product_id, control_def, controlID)
                  VALUES
                          ({}, '{}', '{}')
                
                '''

for i in range(len(nist_definitions)):
    cursor.execute(string2.format(i,(list(nist_definitions.values()))[i], (list(nist_definitions.keys()))[i]))
    conn.commit()